In [1]:
import pandas as pd
import pyodbc
import numpy as np
import plotly.express as px
from datetime import datetime
import statsmodels.api as sm

pd.options.display.float_format = '{:,.2f}'.format
pd.options.display.max_columns = 50
pd.options.display.max_rows = 10

def read_query_file(fileName,extension='.sql'):
    file = open(fileName+extension,'r')
    string = file.read()
    file.close()
    return string

def timestamp():
    return datetime.now().strftime('%Y-%m-%d %I:%M:%S %p')   

def run_query(query):
    cnxn = pyodbc.connect('DSN=edp-workbench-cshub', autocommit=True)
    df = pd.read_sql_query(query,cnxn)
    cnxn.close()
    return df

In [ ]:
run_query("""SELECT * FROM hive.care.l3_asurion_twilio_interaction_interval_summary LIMIT 10""")

In [ ]:
run_query("""SELECT * FROM hive.care.l3_asurion_twilio_interaction_detail WHERE interaction_channel = 'voice' LIMIT 10""")

In [ ]:
locations = run_query("""
          SELECT * FROM  hive.care.l4_asurion_umt_agent_aspect_site_map_ui 
          --LIMIT 100
          WHERE UPPER(Reporting_Site)='ORLANDO' 
          """)
locations

In [ ]:
df = run_query("""
    SELECT
          metric_name,
          aggregate,
          channel,
          count(metric_name) as "occurences"
          FROM care.metric_object
          WHERE 
           (business_unit = 'soluto' or business_unit = 'soluto')
          --and channel = 'voice' 
          GROUP BY metric_name, aggregate, channel
          --ORDER BY count(metric_name) 
          """)


In [ ]:
pd.options.display.max_rows = 69
df[df['channel']!='messaging'].sort_values('metric_name',ascending=True).to_excel('SolutoMetricObjects.xlsx')


In [ ]:
run_query(""" SELECT * FROM hive.care.l3_asurion_soluto_finance_datamart_v1
           LIMIT 10 """)

In [ ]:
run_query("""
    SELECT * 
    FROM care.metric_object mo
    WHERE 1=1
    and mo.business_unit = 'soluto'
    and mo."aggregate"= 'daily'
    and mo."channel"!='messaging'
    AND  (mo."metric_name" = 'crt_num' OR  mo."metric_name" = 'crt_den')
          """)

In [ ]:
run_query(""" SELECT * FROM care.l3_asurion_soluto_finance_datamart_v1
           LIMIT 10 """)

In [ ]:
pd.options.display.max_rows = 50
tables=run_query("""SELECT * FROM INFORMATION_SCHEMA.TABLES WHERE TABLE_Name  like '%metric%' and table_schema = 'care' """)

In [ ]:
tables

In [2]:
crt_df = run_query(read_query_file('SQL\KeyMetrics_ForGroupSelection'))
crt_df

C:\Users\austen.moore\AppData\Local\Temp\ipykernel_34200\943477100.py:23: UserWarning: pandas only supports SQLAlchemy connectable (engine/connection) or database string URI or sqlite3 DBAPI2 connection. Other DBAPI2 objects are not tested. Please consider using SQLAlchemy.
  df = pd.read_sql_query(query,cnxn)


Employee        Date  Total_Resolution_Time  Sessions_Resolved  \
0         542517  2022-07-09              29,529.00              19.00   
1         518896  2022-07-09               5,460.00               9.00   
2         441677  2022-08-11              26,403.00              24.00   
3         549667  2022-08-11              11,791.00              10.00   
4         484134  2022-08-11              10,415.00              10.00   
...          ...         ...                    ...                ...   
1709488   415570  2022-06-08                   0.00               0.00   
1709489   545237  2023-08-12                   0.00               0.00   
1709490   571923  2023-08-12                   0.00               0.00   
1709491   517900  2023-08-12                   0.00               0.00   
1709492   483533  2023-08-12                   0.00               0.00   

         TotalCalls  
0             19.00  
1              9.00  
2             24.00  
3             10.00  
4             10.00  
...             ...  
1709488       16.00  
1709489       11.00  
1709490        9.00  
1709491        6.00  
1709492       16.00  

[1709493 rows x 5 columns]

In [3]:
test=crt_df[crt_df['Date']>=np.datetime64('2023-01-01')].copy()
test[['TotalCalls']].describe()

TotalCalls
count         429,142.00
mean               13.39
std                 7.10
mad (mean)          5.01
mad (median)        3.61
min                 1.00
25%                 9.00
50%                13.00
75%                16.00
max               103.00

In [4]:
import plotly.express as px

px.histogram(test[['TotalCalls']],histnorm='percent')

In [5]:
test[test['TotalCalls']>20]['TotalCalls'].sum()/test[test['TotalCalls']>0]['TotalCalls'].sum()

0.23114555126339772